##     BASE MODEL RF   VIRUSSHARE 80:20 split


In [ ]:
'''
import time
import pickle
import pandas as pd 
import numpy as np
from gensim.models import Word2Vec
import gensim
from matplotlib import pyplot as plt
import plotly.graph_objects as go
from nltk.tokenize import word_tokenize
from sklearn.model_selection import train_test_split
from sklearn import preprocessing,naive_bayes, pipeline, manifold 
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import RobustScaler
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.text import text_to_word_sequence
from tensorflow.keras.preprocessing.sequence import pad_sequences
import seaborn as sns
import re
import nltk
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer
'''

In [ ]:
#plotname=Malware_Original_VIRUSSHARE plotname.split("_")[0] is Malware plotname.split("_")[1] is Original
def API_LENGTH_DISTRIBUTION_PLOT(plotname,Full_Text_name):
    #Count no of API calls in each row
    record_length=[]
    for row in Full_Text_name:
        text=row
        x=len(text.split( ))
        record_length.append(x)
    print("Number of APIS in Longest Sequence is:", max(record_length))
    print("Number of APIS in Shortest Sequence is:", min(record_length))
    Max_Len=max(record_length)
    Min_Len=min(record_length)
    #Counter names to be understood from the respective comment
    #Counter names to be understood from the respective comment
    cnt_0=0
    cnt_1_19=0
    cnt_20_39=0
    cnt_40_59=0
    cnt_60_79=0
    cnt_80_99=0
    cnt_100_149=0
    cnt_150_199=0
    cnt_200_249=0
    cnt_250_299=0
    morethan_300=0
    for x in record_length:
        if x==0:
            cnt_0=cnt_0+1
        elif x<20:
            cnt_1_19=cnt_1_19+1
        elif x<40:
            cnt_20_39=cnt_20_39+1
        elif x<60:
            cnt_40_59=cnt_40_59+1
        elif x<80:
            cnt_60_79 =cnt_60_79+1
        elif x<100:
            cnt_80_99=cnt_80_99+1
        elif x<150:
            cnt_100_149=cnt_100_149+1
        elif x<200:
            cnt_150_199=cnt_150_199+1
        elif x<250:
            cnt_200_249=cnt_200_249+1
        elif x<300:
            cnt_250_299=cnt_250_299+1
        else:
            morethan_300=morethan_300+1

    #print(cnt_0," ",cnt_20," ",cnt_40," ",cnt_60," ",cnt_80," ",cnt_100," ",cnt_120," ",cnt_121)
    # creating the data for plot
    data = {'=0':cnt_0,'>0 and <20':cnt_1_19, '>=20 & <40':cnt_20_39, '>=40 & <60':cnt_40_59,
        '>=60 & <80':cnt_60_79, '>=80 & <100':cnt_80_99, '>=100 & <150':cnt_100_149,
        '>=150 & <200':cnt_150_199,'>=200 & <250':cnt_200_249,'>=250 & <300':cnt_250_299,'>=300':morethan_300 }
    y = list(data.keys())
    x = list(data.values())

    # Plot horizontal bar chart
    plt.figure(figsize = (12, 4))
    bars = plt.barh(y,x)
    # To get data labels
    for  bar in bars:
        width = bar.get_width()
        label_y = bar.get_y() + bar.get_height() / 2
        plt.text(width, label_y, s=f'{width}')

    # Define axes labels
    plt.xlabel("No. of "+plotname.split("_")[0]+" samples in the range")
    plt.ylabel("API Sequence Length \n in "+plotname.split("_")[1]+" Dataset ")
    # Display a bar chart

    #plt.show()
    plot_fname="API_Length_Distribution"+str(plotname)+".eps"
    plt.savefig(plot_fname,format='eps',dpi=1000)
    return Max_Len,Min_Len

In [ ]:
#START Of Method to remove duplicate API   For each distinct API Keep First Occurance and delete all others
def remove_duplicate(api_text):
    return ' '.join(dict.fromkeys(api_text.split()))

In [ ]:
API_Data_all=pd.DataFrame()
API_Data_all=pd.read_csv('../VirusShare_treated.csv')
API_Data_all.shape

In [ ]:
API_Data_all.rename(columns={'file_hash': 'hashcode', 'api': 'API_Sequence','class': 'MalwareType'}, inplace=True)

In [ ]:
API_Data = API_Data_all.loc[API_Data_all['MalwareType'].isin(['Trojan','Virus','Adware','Backdoor','Downloader','Worms','Agent','Ransomware'])]
API_Data=API_Data.reset_index(drop=True)

In [ ]:
#
def plot_lenAPISEQ_vs_FreqAPISEQ(TEXTDATA,pltname):
    record_length=[]
    for row in TEXTDATA:
        text=row
        x=len(text.split())
        record_length.append(x)
    print("Number of APIS in Longest Sequence is:", max(record_length))
    print("Number of APIS in Shortest Sequence is:", min(record_length))
    x_list=[]
    y_list=[]
    for cnt in range(1,max(record_length)+1):
        x_list.append(cnt)
        y_list.append(record_length.count(cnt))
        #print(cnt," ",record_length.count(cnt))
    plt.figure(figsize = (12, 4))
    #plt.title(dfname_str)
    # Define axes labels
    plt.xlabel("Length of API Sequence")
    plt.ylabel("Frequency of such API Sequences")
    plt.plot(x_list, y_list)   
    # Displaying the line chart  
    #plt.show()   
    plt.savefig(pltname+"API Sequence distribution length wise.eps",format='eps',dpi=1000)  

In [ ]:
MalwareLabel=preprocessing.LabelEncoder()
API_Data['MalwareTypeId']=MalwareLabel.fit_transform(API_Data['MalwareType'])

In [ ]:
Full_Text_org=API_Data['API_Sequence']
Full_Text_org.shape

In [ ]:
API_LENGTH_DISTRIBUTION_PLOT("Malware_Original_VIRUSSHARE",Full_Text_org)

In [ ]:
#Full_Text_org_Dup_Removed=Full_Text_org.apply(remove_duplicate)
Full_Text_org_Dup_Removed=Full_Text_org
Full_Text_org_Dup_Removed.shape

In [ ]:
plot_lenAPISEQ_vs_FreqAPISEQ(Full_Text_org_Dup_Removed,"Full_Text_org_Dup_Removed")

In [ ]:
API_LENGTH_DISTRIBUTION_PLOT("Malware_DupRemoved_VirusShare",Full_Text_org_Dup_Removed)

In [ ]:
API_Data['API_Sequence']=Full_Text_org_Dup_Removed
Full_Text_org_Dup_Removed=API_Data['API_Sequence']

In [ ]:
#'Adware','Agent','Backdoor','Downloader','Ransomware','Trojan','Virus','Worms'
API_Data_Adware = API_Data[API_Data["MalwareTypeId"] == 0]
API_Data_Adware=API_Data_Adware.reset_index(drop=True)

API_Data_Agent = API_Data[API_Data["MalwareTypeId"] == 1]
API_Data_Agent=API_Data_Agent.reset_index(drop=True)


API_Data_Backdoor = API_Data[API_Data["MalwareTypeId"] == 2]
API_Data_Backdoor=API_Data_Backdoor.reset_index(drop=True)

API_Data_Downloader = API_Data[API_Data["MalwareTypeId"] == 3]
API_Data_Downloader=API_Data_Downloader.reset_index(drop=True)

API_Data_Ransomware = API_Data[API_Data["MalwareTypeId"] == 4]
API_Data_Ransomware=API_Data_Ransomware.reset_index(drop=True)


API_Data_Trojan = API_Data[API_Data["MalwareTypeId"] == 5]
API_Data_Trojan=API_Data_Trojan.reset_index(drop=True)

API_Data_Virus = API_Data[API_Data["MalwareTypeId"] == 6]
API_Data_Virus=API_Data_Virus.reset_index(drop=True)

API_Data_Worms = API_Data[API_Data["MalwareTypeId"] == 7]
API_Data_Worms=API_Data_Worms.reset_index(drop=True)
#[API_Data_Adware,API_Data_Agent,API_Data_Backdoor,API_Data_Downloader,API_Data_Ransomware,API_Data_Trojan,API_Data_Virus,API_Data_Worms]

In [ ]:
dflist_temp=[API_Data_Adware,API_Data_Agent,API_Data_Backdoor,API_Data_Downloader,API_Data_Ransomware,API_Data_Trojan,API_Data_Virus,API_Data_Worms]
API_Data_ORG = pd.concat(dflist_temp)

In [ ]:
API_Data_ORG_Full_Text=API_Data_ORG['API_Sequence']

In [ ]:
#API_Data_ORG_Full_Text_Dup_Removed=API_Data_ORG_Full_Text.apply(remove_duplicate)
API_Data_ORG_Full_Text_Dup_Removed=API_Data_ORG_Full_Text

In [ ]:
plot_lenAPISEQ_vs_FreqAPISEQ(API_Data_Adware['API_Sequence'],"API_Data_Adware")

In [ ]:
plot_lenAPISEQ_vs_FreqAPISEQ(API_Data_Agent['API_Sequence'],"API_Data_Agent")

In [ ]:
plot_lenAPISEQ_vs_FreqAPISEQ(API_Data_Backdoor['API_Sequence'],"API_Data_Backdoor")

In [ ]:
plot_lenAPISEQ_vs_FreqAPISEQ(API_Data_Downloader['API_Sequence'],"API_Data_Downloader")

In [ ]:
plot_lenAPISEQ_vs_FreqAPISEQ(API_Data_Ransomware['API_Sequence'],"API_Data_Ransomware")

In [ ]:
plot_lenAPISEQ_vs_FreqAPISEQ(API_Data_Trojan['API_Sequence'],"API_Data_Trojan")

In [ ]:
plot_lenAPISEQ_vs_FreqAPISEQ(API_Data_Virus['API_Sequence'],"API_Data_Virus")

In [ ]:
plot_lenAPISEQ_vs_FreqAPISEQ(API_Data_Worms['API_Sequence'],"API_Data_Worms")

In [ ]:
def plot_TFIDF_Feature_change(org_length,new_length,dfname_str):
    # Combine the lists using zip 
    combined_length = list(zip(org_length, new_length)) 

    # Sort the combined list based on the first list 
    sorted_combined_length = sorted(combined_length) 

    # Unzip the sorted combined list back into two lists 
    sorted_org_length, sorted_new_length = zip(*sorted_combined_length) 

    # Convert back to lists if needed 
    sorted_org_length = list(sorted_org_length) 
    sorted_new_length = list(sorted_new_length) 

    # Output the sorted lists 
    #print("Sorted List 1:", sorted_org_length[1:100]) 
    #print("Sorted List 2:", sorted_new_length[1:100]) 
    plt.figure(figsize = (12, 4))
    #plt.title(dfname_str)
    # Define axes labels
    plt.xlabel("Original Length Distribution of "+dfname_str.split("_")[2])
    plt.ylabel("Updated Length Distribution of \n"+dfname_str.split("_")[2])
    plt.plot(sorted_org_length, sorted_new_length)   

    # Displaying the line chart  
    #plt.show()   
    plt.savefig(dfname_str+".eps",format='eps',dpi=1000)   
    return

In [ ]:
Min_Count=1
Vector_size=200

In [ ]:
def prune_API_by_TFIDF(record):
    APINAMES=[]
    reclen=len(record)
    col_pos=0
    for col_name in prune_API_by_TFIDF.TFIDF_df_cols:
        #TF_IDF_VAR=np.var(prune_API_by_TFIDF.TFIDF_df.iloc[prune_API_by_TFIDF.i_loc][col_pos])
        #TF_IDF Value of each API
        TF_IDF_VAL=prune_API_by_TFIDF.TFIDF_df.iloc[prune_API_by_TFIDF.i_loc][col_pos]
        if (TF_IDF_VAL>prune_API_by_TFIDF.val):     #Test with 0.12 0.11
            #print(TFIDF_df_cols[col_pos],"  ",col_name," ",TFIDF_df.iloc[prune_API_by_TFIDF.i_loc][col_pos])
            APINAMES.append(col_name)
            #print("APINAME: ",col_name,"Threshold: ", prune_API_by_TFIDF.val," Actual: ", TF_IDF_VAL)
        col_pos=col_pos+1
    #print(prune_API_by_TFIDF.i_loc)
    #print("++++++++++")
    #print("APINAMES LIST:  ",APINAMES)
    #print("++++++++++")
    #APINAMES is the selected APIS for record
    temprow=[]
    temprow_for_org=[]
    row_list=record.split()
    #print("row_list: ", row_list)
    for api_name in row_list:
        #print(api_name)
        if api_name.lower() in APINAMES:
            temprow.append(api_name)
    #print(temprow)
    #to check only
    temprow_for_org=[]
    for api_name in row_list:
        temprow_for_org.append(api_name)
    #ends to check only
    #print(temprow_for_org)
    
    #print(prune_API_by_TFIDF.i_loc," ORG LRNGTH: ",len(row_list)," Slected APINAMES Length: ",len(APINAMES)," New Length: ", len(temprow),"No of APIS Removed: ", len(row_list)-len(temprow))
    #print(" ORG LRNGTH: ",len(row_list),"         New Length: ", len(temprow),"          No of APIS Removed: ", len(row_list)-len(temprow))
    prune_API_by_TFIDF.org_length.append(len(row_list))
    
    prune_API_by_TFIDF.i_loc=prune_API_by_TFIDF.i_loc+1
    if len(temprow)==0:
        prune_API_by_TFIDF.new_length.append(len(temprow_for_org))
        return temprow_for_org
    else:
        prune_API_by_TFIDF.new_length.append(len(temprow))
        return temprow

In [ ]:
def TFIDF_Prune_classWise(dfname_obj,dfname_str,dfname_str_var):
    #print("Starts: ",dfname_str)
    #print(dfname_obj.MalwareTypeId.value_counts())
    #print(dfname_str)
    #dfname_obj['MalwareTypeId']=15
    Full_Text_fun=dfname_obj['API_Sequence']
    API_LENGTH_DISTRIBUTION_PLOT(dfname_str.split("_")[2]+"_ORIGINAL_VirusShare",Full_Text_fun)
    #Call method to remove Duplicate API
    #Full_Text_fun=Full_Text_fun.apply(remove_duplicate)
    API_LENGTH_DISTRIBUTION_PLOT(dfname_str.split("_")[2]+"_DuplicateRemoved_VirusShare",Full_Text_fun)
    #TFIDF weight finder
    tfidf_vectorizer = TfidfVectorizer()
    tfidf_matrix = tfidf_vectorizer.fit_transform(Full_Text_fun)
    terms = tfidf_vectorizer.get_feature_names_out()
    print("No. of features: ", len(terms))
    #print(terms)
    prune_API_by_TFIDF.TFIDF_df = pd.DataFrame(tfidf_matrix.toarray(), columns=terms)
    prune_API_by_TFIDF.TFIDF_df_cols=prune_API_by_TFIDF.TFIDF_df.columns.values.tolist()
    
    #For The variance selector at method prune_API_by_TFIDF starts
    TFIDF_Prune_classWise.var_Dict[dfname_str]=dfname_str_var
    prune_API_by_TFIDF.val=TFIDF_Prune_classWise.var_Dict[dfname_str]
    ##For The variance selector at method prune_API_by_TFIDF Ends
    
    prune_API_by_TFIDF.i_loc=0
    prune_API_by_TFIDF.org_length=[]
    prune_API_by_TFIDF.new_length=[]
    Full_Text_TFIDF_pruned=Full_Text_fun.apply(prune_API_by_TFIDF)
    #print(prune_API_by_TFIDF.org_length)
    #print(prune_API_by_TFIDF.new_length)
    
    
    # Start Plot reduction in API SEQUENCE LENGTH Sample lists 
    org_length = prune_API_by_TFIDF.org_length
    new_length = prune_API_by_TFIDF.new_length 

    plot_TFIDF_Feature_change(org_length,new_length,dfname_str)
    # End Plot reduction in API SEQUENCE LENGTH Sample lists 
    
    
    #Converts the list of API Bigrams string of API Bigrams 
    Full_Text_TFIDF_pruned_f=[' '.join(map(str, l)) for l in Full_Text_TFIDF_pruned]
    
    API_LENGTH_DISTRIBUTION_PLOT(dfname_str.split("_")[2]+"_TFIDFPrunned",Full_Text_TFIDF_pruned_f)
    
    dfname_obj['API_Sequence']=Full_Text_TFIDF_pruned_f
    
    #print("Ends: ",dfname_str)

In [ ]:
#TFIDF_Prune_classWise.var_Dict={"API_Data_Adware":0.07,"API_Data_Agent":0.06,"API_Data_Backdoor":0.05,"API_Data_Trojan":0.0,"API_Data_Virus":0.0,"API_Data_Worms":0.11}
TFIDF_Prune_classWise.var_Dict=TFIDF_Prune_classWise_VAR_Dict
#dfname_str="API_Data_Agent"
#print(var_Dict[dfname_str])
#var_Dict[dfname_str]=0.001
#print(var_Dict)


In [ ]:
dflist=[API_Data_Adware,API_Data_Agent,API_Data_Backdoor,API_Data_Downloader,API_Data_Ransomware,API_Data_Trojan,API_Data_Virus,API_Data_Worms]
#[API_Data_Adware,API_Data_Agent,API_Data_Backdoor,API_Data_Downloader,API_Data_Ransomware,API_Data_Trojan,API_Data_Virus,API_Data_Worms]

In [ ]:

if(TFIDF_Prune_classWise.var_Dict['API_Data_Adware']>0):
    TFIDF_Prune_classWise(API_Data_Adware,'API_Data_Adware',TFIDF_Prune_classWise.var_Dict['API_Data_Adware'])

In [ ]:

if(TFIDF_Prune_classWise.var_Dict['API_Data_Agent']>0):
    TFIDF_Prune_classWise(API_Data_Agent,'API_Data_Agent',TFIDF_Prune_classWise.var_Dict['API_Data_Agent'])

In [ ]:

if(TFIDF_Prune_classWise.var_Dict['API_Data_Backdoor']>0):
    TFIDF_Prune_classWise(API_Data_Backdoor,'API_Data_Backdoor',TFIDF_Prune_classWise.var_Dict['API_Data_Backdoor'])

In [ ]:

if(TFIDF_Prune_classWise.var_Dict['API_Data_Downloader']>0):
    TFIDF_Prune_classWise(API_Data_Downloader,'API_Data_Downloader',TFIDF_Prune_classWise.var_Dict['API_Data_Downloader'])

In [ ]:

if(TFIDF_Prune_classWise.var_Dict['API_Data_Ransomware']>0):
    TFIDF_Prune_classWise(API_Data_Ransomware,'API_Data_Ransomware',TFIDF_Prune_classWise.var_Dict['API_Data_Ransomware'])

In [ ]:

if(TFIDF_Prune_classWise.var_Dict['API_Data_Trojan']>0):
    TFIDF_Prune_classWise(API_Data_Trojan,'API_Data_Trojan',TFIDF_Prune_classWise.var_Dict['API_Data_Trojan'])

In [ ]:

if(TFIDF_Prune_classWise.var_Dict['API_Data_Virus']>0):
    TFIDF_Prune_classWise(API_Data_Virus,'API_Data_Virus',TFIDF_Prune_classWise.var_Dict['API_Data_Virus'])

In [ ]:

if(TFIDF_Prune_classWise.var_Dict['API_Data_Worms']>0):
    TFIDF_Prune_classWise(API_Data_Worms,'API_Data_Worms',TFIDF_Prune_classWise.var_Dict['API_Data_Worms'])

In [ ]:
print(TFIDF_Prune_classWise.var_Dict)

In [ ]:
dflist=[API_Data_Adware,API_Data_Agent,API_Data_Backdoor,API_Data_Downloader,API_Data_Ransomware,API_Data_Trojan,API_Data_Virus,API_Data_Worms]
API_Data_PRUNED = pd.concat(dflist)

In [ ]:
Full_Text_TFIDF_pruned=API_Data_PRUNED['API_Sequence']
Full_Text_TFIDF_pruned.shape

In [ ]:
API_LENGTH_DISTRIBUTION_PLOT("Malware_SkipGramVariance_pruned_VirusShare",Full_Text_TFIDF_pruned)

In [ ]:
def Get_Each_Seq_Length(Full_Text_Data):
    seq_length=[]
    for seq in Full_Text_Data:
        row_list=seq.split()
        seq_length.append(len(row_list))
    return seq_length

In [ ]:
Full_Text_org_Dup_Removed_len=Get_Each_Seq_Length(API_Data_ORG_Full_Text_Dup_Removed)
Full_Text_org_len=Get_Each_Seq_Length(API_Data_ORG_Full_Text)
Full_Text_TFIDF_pruned_len=Get_Each_Seq_Length(Full_Text_TFIDF_pruned)

In [ ]:
plot_TFIDF_Feature_change(Full_Text_org_len,Full_Text_TFIDF_pruned_len,"API_LengthVariation_VirusShare")

In [ ]:
plot_TFIDF_Feature_change(Full_Text_org_Dup_Removed_len,Full_Text_TFIDF_pruned_len,"API_LengthVariation_DUPRemoved_VirusShare")

In [ ]:
plot_TFIDF_Feature_change(Full_Text_org_len,Full_Text_org_Dup_Removed_len,"API_LengthVariation_ORGvDUPR_VirusShare")

In [ ]:
#Count Empty Strings in API_Sequence
#print((API_Data['API_Sequence']=='').sum())
API_Data_filtered = API_Data_PRUNED[API_Data_PRUNED['API_Sequence'] != '']
#Reset Index
API_Data_filtered=API_Data_filtered.reset_index(drop=True)

In [ ]:
#'Adware','Agent','Backdoor','Downloader','Trojan','Virus','Worms'
API_Data_filtered.MalwareType.value_counts()

In [ ]:
Full_Text_prunned=API_Data_filtered['API_Sequence']

In [ ]:
Max_Len,Min_Len=API_LENGTH_DISTRIBUTION_PLOT("_After_TFIDF_Prunning_Final",Full_Text_prunned)

In [ ]:
#Full_Text_t=Full_Text_org.apply(api_preprocess)
Full_Text_t=Full_Text_prunned

In [ ]:
# START FEATURE(API) SELCTION
# Train the Word2Vec model  before duplicate removal to check API with less variance
Min_Count=1
Vector_size=200
sentences = [sentence.split() for sentence in Full_Text_t]
w2v_model = Word2Vec(sentences, window=10, min_count=Min_Count,vector_size=Vector_size, workers=4,sg=1)  

In [ ]:
#print("w2v_model.corpus_total_words ", w2v_model.corpus_total_words, "w2v_model.corpus_count ",w2v_model.corpus_count)

In [ ]:
# Tokenize the text data
#tokenizer = Tokenizer()
tokenizer_FS = Tokenizer(lower=False,split=' ',filters='!"%&()*+,-./:;<=>[\\]^`{|}~\t\n',)
#It will first create a dictionary for the entire corpus (a mapping of each word token and its unique 
#integer index index) (Tokenizer.fit_on_text())
tokenizer_FS.fit_on_texts(Full_Text_t)

In [ ]:
#tokenizer_FS.word_index

In [ ]:
#Call method to remove Duplicate API
#Full_Text=Full_Text_t_pruned.apply(remove_duplicate)
#Full_Text=Full_Text_t_pruned
Full_Text=Full_Text_t

In [ ]:
#create dictionary of API
reverse_word_map = dict(map(reversed, tokenizer_FS.word_index.items()))

In [ ]:
#use index to get name of API
#reverse_word_map[75]

In [ ]:
#generate weight vector using index
#w2v_model.wv[reverse_word_map[75]]

In [ ]:
#w2v_model.wv['getnativesysteminfo']

In [ ]:
#w2v_model.wv[reverse_word_map[1]]

In [ ]:
Full_Text_tokenized = tokenizer_FS.texts_to_sequences(Full_Text)

In [ ]:
vocab_size = len(tokenizer_FS.word_index) + 1

In [ ]:
print("Number of distinct API's: i.e. vocab_size",vocab_size)

In [ ]:
word_embedding_matrix=[] 
for vocab_index in range(1,vocab_size):      #281 to be replaced with vocab_size
    word=reverse_word_map[vocab_index]
    word_embedding_matrix.append(w2v_model.wv[word])

In [ ]:
#len(word_embedding_matrix[79])

In [ ]:
#word_embedding_matrix[79]

In [ ]:
#Full_Text_tokenized

In [ ]:
Mal_Class=API_Data_filtered['MalwareTypeId']

In [ ]:
X_train,X_test, y_train,y_test=train_test_split(Full_Text_tokenized,Mal_Class, test_size=0.2, random_state=27,stratify=Mal_Class)

In [ ]:
#count of ppropertionate classes in train and test
#'Adware','Agent','Backdoor','Downloader','Ransomware','Trojan','Virus','Worms'
from collections import Counter 
print('Train', Counter(y_train))
print('Test', Counter(y_test))

In [ ]:
test_set_size=y_test.size
print("Test Set Size: ",test_set_size)

In [ ]:
X_train_cnn=X_train
X_train_ML=X_train

In [ ]:
X_test_cnn=X_test
X_test_ML=X_test

In [ ]:
#ML Algorithms Start Here

In [ ]:
#X_train_ML[10]

In [ ]:
#=============================================
# Vectorize the data
#Convert the preprocessed text data to a vector representation using the Word2Vec model
'''def vectorize(sentences):
    #words=sentences.split()
    words=[]
    for i in sentences:
        words.append(reverse_word_map[i])
    #print (words)
    #print (w2v_model.wv[reverse_word_map[sentences[0]]])
    words_vecs=[w2v_model.wv[word] for word in words if word in w2v_model.wv]
    if len(words_vecs) == 0:
        return np.zeros(Vector_size)
    words_vecs=np.array(words_vecs)
    return words_vecs.mean(axis=0)
    #return words_vecs'''
#word_embedding_matrix_pca[]    280x20 
def vectorize(sentences):
    #words=sentences.split()
    words=[]
    for i in sentences:
        words.append(i)
    #print (words)
    #print (w2v_model.wv[reverse_word_map[sentences[0]]])
    words_vecs=[word_embedding_matrix[word-1] for word in words if reverse_word_map[word] in w2v_model.wv]
    if len(words_vecs) == 0:
        return np.zeros(Vector_size)
    words_vecs=np.array(words_vecs)
    #print(words_vecs)
    return words_vecs.mean(axis=0)
    #return words_vecs

In [ ]:
#print (vectorize(X_train[1]))
X_train_ML_F=np.array([vectorize(sentence) for sentence in X_train_ML])

In [ ]:
#scaler_train = RobustScaler()
#embedding_matrix_scaled3 = scaler.fit_transform(embedding_matrix3)
#scaler_train = MinMaxScaler()
scaler_train = StandardScaler()
X_train_scaled = scaler_train.fit_transform(X_train_ML_F)
#X_train_scaled=X_train_ML_F

In [ ]:
X_test_ML_F=np.array([vectorize(sentence) for sentence in X_test_ML])

In [ ]:
#scaler_test = RobustScaler()
#embedding_matrix_scaled3 = scaler.fit_transform(embedding_matrix3)
#scaler_test = MinMaxScaler()
scaler_test = StandardScaler()
X_test_scaled = scaler_test.fit_transform(X_test_ML_F)
#X_test_scaled=X_test_ML_F

In [ ]:
from sklearn.naive_bayes import MultinomialNB
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from numpy import std
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedStratifiedKFold
from matplotlib import pyplot
from sklearn.metrics import confusion_matrix, classification_report,accuracy_score, precision_score, recall_score, f1_score
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedStratifiedKFold
from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import precision_recall_curve, roc_curve, auc
import seaborn as sn
import matplotlib.pyplot as plt
from sklearn.preprocessing import LabelBinarizer

import matplotlib.pyplot as plt
from sklearn.metrics import RocCurveDisplay
from sklearn.metrics import roc_curve, auc
from itertools import cycle

In [ ]:
'''
#G_scaler_Robust = RobustScaler()
#G_scaler_MinMax = MinMaxScaler()
G_scaler_test = StandardScaler()
X_testNB_scaled = G_scaler_test.fit_transform(X_test_ML_F)
X_trainNB_scaled = G_scaler_test.fit_transform(X_train_ML_F)
clf_MultinNB = MultinomialNB(alpha=0.001)
#Start Training MultiNomialNB

clf_MultinNB = clf_MultinNB.fit(X_trainNB_scaled, y_train)
#CONF MATRIX and Classification Report LR Model

y_probs_MNB = clf_MultinNB.predict_proba(X_testNB_scaled)


y_predict_MNB = clf_MultinNB.predict(X_testNB_scaled)

conf_matrix_MNB=confusion_matrix(y_test, y_predict_MNB)
print(conf_matrix_MNB)
print(f'{classification_report(y_test, y_predict_MNB)}')
'''

In [ ]:
target_names=['Adware','Agent','Backdoor','Downloader','Ransomware','Trojan','Virus','Worms']
n_classes=8
colors = cycle(["aqua", "darkorange", "cornflowerblue","blue","red","green","yellow","magenta"])

In [ ]:
#Heatmapof the confusion matrix LR Model
import seaborn as sn
import matplotlib.pyplot as plt
#In this section we use a LabelBinarizer to binarize the target by one-hot-encoding in a OvR fashion. 
#This means that the target of shape (n_samples,) is mapped to a target of shape (n_samples, n_classes).
#FOR ROC PLOT
from sklearn.preprocessing import LabelBinarizer

import matplotlib.pyplot as plt
from sklearn.metrics import RocCurveDisplay
from sklearn.metrics import roc_curve, auc
from itertools import cycle

label_binarizer = LabelBinarizer().fit(y_train)
y_onehot_test = label_binarizer.transform(y_test)
y_onehot_test.shape  # (n_samples, n_classes)
#We can as well easily check the encoding of a specific class:
#label_binarizer.transform([6])
#ROC curve showing a specific class
#class_of_interest = 3
#class_id = np.flatnonzero(label_binarizer.classes_ == class_of_interest)[0]
#class_id

In [ ]:
# RF Starts
#ORG clf_RF = RandomForestClassifier(n_estimators=1000, criterion = 'entropy', bootstrap=True,max_depth=100)
clf_RF = RandomForestClassifier(n_estimators=200, criterion = 'entropy', bootstrap=True,max_depth=1000)

In [ ]:
#DUMP clf_RF Model
clf_RF = clf_RF.fit(X_train_scaled, y_train)

In [ ]:
#CONF MATRIX and Classification Report RF Model

y_probs_RF = clf_RF.predict_proba(X_test_scaled)

#Start time RF
RF_start_time = time.process_time()
y_predict_RF = clf_RF.predict(X_test_scaled)
#End time RF for MTTD
RF_elapsed_time = time.process_time() - RF_start_time

print("RF Full Detection Time",RF_elapsed_time)
print("RF Mean Time to Detection MTTD",RF_elapsed_time/test_set_size)
print("RF MTTD in ms",(RF_elapsed_time/test_set_size)*1000)
conf_matrix_RF=confusion_matrix(y_test, y_predict_RF)
print(conf_matrix_RF)
print(f'{classification_report(y_test, y_predict_RF)}')

In [ ]:
%%capture RF_OUTPUT_LABELS
print(list(y_predict_RF))

In [ ]:
# Save the captured output to a text file
with open('RF_OUTPUT_LABELS.txt', 'w') as file:
    file.write(RF_OUTPUT_LABELS.stdout)
del RF_OUTPUT_LABELS

In [ ]:
%%capture capRF
print("RF Full Detection Time",RF_elapsed_time)
print("RF Mean Time to Detection MTTD",RF_elapsed_time/test_set_size)
print("RF MTTD in ms",(RF_elapsed_time/test_set_size)*1000)
conf_matrix_RF=confusion_matrix(y_test, y_predict_RF)
print(conf_matrix_RF)
print(f'{classification_report(y_test, y_predict_RF)}')

In [ ]:
# Save the captured output to a text file
with open('RF_training_output.txt', 'w') as file:
    file.write(capRF.stdout)
del capRF

In [ ]:
#Heatmapof the confusion matrix RF Model
import seaborn as sn
import matplotlib.pyplot as plt
plt.figure(figsize = (10,7))

x_label=target_names #x_label=['Adware','Agent','Backdoor','Trojan','Virus','Worms']
y_label=target_names #y_label=['Adware','Agent','Backdoor','Trojan','Virus','Worms']


sn.heatmap(conf_matrix_RF, annot=True,cmap="Greens",fmt='.4g',annot_kws={"size": 14},xticklabels=x_label, yticklabels=y_label)
plt.xlabel('Predicted')
plt.ylabel('Actual')
plt.savefig("RF_cfm.eps",format='eps',dpi=1200)

In [ ]:
#ROC-AUC Plot for RF Model
#target_names=['Adware','Agent','Backdoor','Trojan','Virus','Worms']
#n_classes=6
# store the fpr, tpr, and roc_auc for all averaging strategies
fpr, tpr, roc_auc = dict(), dict(), dict()

# Compute micro-average ROC curve and ROC area start
fpr["micro"], tpr["micro"], _ = roc_curve(y_onehot_test.ravel(), y_probs_RF.ravel())
roc_auc["micro"] = auc(fpr["micro"], tpr["micro"])
#print(f"Micro-averaged One-vs-Rest ROC AUC score:\n{roc_auc['micro']:.2f}")
# Compute micro-average ROC curve and ROC area end


#compute fpr,tpr auc part for plot
for i in range(n_classes):
    fpr[i], tpr[i], _ = roc_curve(y_onehot_test[:, i],y_probs_RF[:, i])
    roc_auc[i] = auc(fpr[i], tpr[i])

#Compute macro-average ROC curve and ROC area start 
fpr_grid = np.linspace(0.0, 1.0, 1000)
#Interpolate all ROC curves at these points
mean_tpr = np.zeros_like(fpr_grid)
for i in range(n_classes):
    mean_tpr += np.interp(fpr_grid, fpr[i], tpr[i])  # linear interpolation
# Average it and compute AUC
mean_tpr /= n_classes
fpr["macro"] = fpr_grid
tpr["macro"] = mean_tpr
roc_auc["macro"] = auc(fpr["macro"], tpr["macro"])
#print(f"Macro-averaged One-vs-Rest ROC AUC score:\n{roc_auc['macro']:.2f}")
### Compute macro-average ROC curve and ROC area end

#Plot starts
fig, ax = plt.subplots(figsize=(8, 8))

plt.plot(
    fpr["micro"],
    tpr["micro"],
    label=f"micro-average (AUC = {roc_auc['micro']:.2f})",
    color="deeppink",
    linestyle=":",
    linewidth=4,
)

plt.plot(
    fpr["macro"],
    tpr["macro"],
    label=f"macro-average (AUC = {roc_auc['macro']:.2f})",
    color="navy",
    linestyle=":",
    linewidth=4,
)

#colors = cycle(["aqua", "darkorange", "cornflowerblue","blue","red","green"])
for class_id, color in zip(range(n_classes), colors):
    RocCurveDisplay.from_predictions(
        y_onehot_test[:, class_id],
        y_probs_RF[:, class_id],
        name=f"{target_names[class_id]}",
        color=color,
        ax=ax,
    )

plt.plot([0, 1], [0, 1], "k--",label="")
plt.axis("square")
plt.xlabel("False Positive Rate")
plt.ylabel("True Positive Rate")
#plt.title("Receiver Operating Characteristic")
plt.yticks(np.arange(0, 1.1, 0.1))
plt.xticks(np.arange(0, 1.1, 0.1))
plt.legend()

plt.savefig("RF_ROC_AUC.eps",format='eps',dpi=1200)
plt.show()

In [ ]:
# precision recall curve for RF MODEL
from sklearn.metrics import precision_recall_curve, roc_curve, auc
#target_names=['Adware','Agent','Backdoor','Trojan','Virus','Worms']
precision = dict()
recall = dict()
auc_score= dict()
#n_classes=6
plt.figure(figsize=(8,8))
for i in range(n_classes):
    precision[i], recall[i], _ = precision_recall_curve(y_onehot_test[:, i],y_probs_RF[:, i])
    auc_score[i] = auc(recall[i], precision[i])
    #labelname=f"target_names[i]+' '+str(round(auc_score[i],2))",
    labelname=target_names[i]+" (AUC=%.2f"%auc_score[i]+")"
    plt.plot(recall[i], precision[i], lw=2, label=labelname)
    
#plt.plot([1, 0], [0, 0], "k--",label="")
plt.xlabel("Recall")
plt.ylabel("Precision")
#plt.legend(loc="best")
plt.yticks(np.arange(0, 1.1, 0.1))
plt.xticks(np.arange(0, 1.1, 0.1))
plt.legend()
#plt.title("precision vs. recall curve")
plt.savefig("RF_Pre_Recall.eps",format='eps',dpi=1200)
plt.show()

In [ ]:
#ENS CLassifier Ends

In [ ]:
#For statistical significance test Base model to Ensemble Model

In [ ]:
#making test labels as numpy array
test_labels = np.array(y_test)   #Original Class labels
#print (test_labels)

#Base model prediction for X_test and give prediction probabilities as y_probs_base
#y_probs_base = Base_1DCNN.predict(X_test)
#pred_proba_LSTM = model_LSTM.predict(X_test_LSTM)

#Convert prediction probabilities into integers
#y_preds_base = y_probs_base.argmax(axis=1)
#y_preds_base = pred_proba_LSTM.argmax(axis=1)  # THE Base Model LSTM predicted classes 
y_preds_base=y_predict_RF  # THE BASE classifier  RF predicted class labels 


In [ ]:
%%capture capmcc
#The Matthews correlation coefficient is used in machine learning as a measure of the quality of 
#binary and multiclass classifications. It takes into account true and false positives and negatives 
#and is generally regarded as a balanced measure which can be used 
#even if the classes are of very different sizes. 
#The MCC is in essence a correlation coefficient value between -1 and +1. 
#A coefficient of +1 represents a perfect prediction, 0 an average random prediction and -1 an inverse prediction.
#The statistic is also known as the phi coefficient. 
#Output interpretation
#The Matthews correlation coefficient (+1 represents a perfect prediction, 
#0 an average random prediction 
#and -1 and inverse prediction).

from sklearn.metrics import matthews_corrcoef
print("Matthews correlation coefficient: ")
print("MCC RF Classifier",matthews_corrcoef(test_labels, y_preds_base))
print("MX Count: ",Max_Len," Min Count: ", Min_Len)

In [ ]:
# Save the captured output to a text file
with open('capture_mcc_output.txt', 'w') as file:
    file.write(capmcc.stdout)
del capmcc

In [ ]:
print("Matthews correlation coefficient: ")
print("MCC RF Classifier",matthews_corrcoef(test_labels, y_preds_base))
print("MX Count: ",Max_Len," Min Count: ", Min_Len)